In [151]:
# imports
import pandas as pd
import numpy as np
pd.set_option('display.max_colwidth', 140)
pd.set_option('display.width', 2000)
import sys,os
from IPython.core.debugger import Tracer
from IPython.core.debugger import BdbQuit_excepthook
%matplotlib inline
%load_ext line_profiler
import matplotlib.pyplot as plt
import matplotlib
import nltk
import io
import json
import time
from pandas import ExcelWriter
from ast import literal_eval
import hashlib
import unicodedata
import subprocess
import datetime
m = hashlib.md5()
from nltk.metrics import *
from nltk import pos_tag, word_tokenize
from nltk.corpus import stopwords
import zipfile
import pymongo
import re
import random
from tqdm import tqdm

The line_profiler extension is already loaded. To reload it, use:
  %reload_ext line_profiler


In [152]:
import importlib
import tqdm
importlib.reload(tqdm)
from tqdm import tqdm

# Experiment config

In [153]:
EXP_NAME = 'triviaqa_base'
EVAL_SET = 'train' # train, dev
WRITE_EVIDENCE = True
SEARCHRESULTS_FROM_FILES = True
FILES_PER_QUESTION = 20

# TriviaQA
USE_TRIVIAQA_DEV = True
USE_TRIVIAQA_TRAIN = True

# CopmlexWebQuestions
#! if USE_TRIVIAQA_DEV is False, then CopmlexWebQuestions dev is used
USE_COMPWEBQ_TRAIN = False
ADD_SPLITS_TO_TRAIN = True

# GENERAL
PRODUCE_ONLY_SAMPLE = False
EVIDENCE_DIR = '/Users/alontalmor/Documents/dev/datasets/triviaqa/triviaqa-rc/'

# Tests
CALC_ANSWER_IN_GOOGLE_PERC = True

# Loading Dataset

## Dev Set

### TriviaQA

In [154]:
if USE_TRIVIAQA_DEV and EVAL_SET == 'dev':
    with zipfile.ZipFile('../data/TriviaQA/unfiltered-web-dev.json.zip','r') as myzip:
        with myzip.open('unfiltered-web-dev.json') as myfile:
            questions = json.load(myfile)
            triviaqa_dataset = pd.DataFrame(questions['Data'])
            
    # empty entity pages
    triviaqa_dataset['EntityPages'] = np.empty((len(triviaqa_dataset), 0)).tolist()

    # empty search results
    triviaqa_dataset['SearchResults']  = triviaqa_dataset['SearchResults'].astype(object)
    triviaqa_dataset['SearchResults'] = np.empty((len(triviaqa_dataset), 0)).tolist()

### ComplexWebQuestions

In [155]:
# comparing web triavia-rc dev number of question to unfiltered number of questions
if not USE_TRIVIAQA_DEV and EVAL_SET == 'dev':
    rl_input_df = pd.DataFrame()
    #data_dir = '/Users/alontalmor/Dropbox/Apps/WebKB/webkb_dev_data/RL_preproc_data/rl_cascade1_epoch0-8/'
    data_dir = '../data/V2_dev_splitpoints/'
    filename = 'dev.json.zip'
    if filename.find('.json.zip') > -1:
        print(filename)
        with zipfile.ZipFile(data_dir + filename, 'r') as myzip:
            with myzip.open(filename.replace('.zip', '')) as myfile:
                curr_batch = pd.DataFrame(json.load(myfile))
        curr_batch = curr_batch[(curr_batch[['split_part1', 'split_part2']].isnull(
        ) * 1.0).sum(axis=1) == 0]  # removing null values
        curr_batch['traj_id'] = curr_batch['ID'] + curr_batch['comp'] + curr_batch['split_part1'].str.replace(" ","") \
                                + ',' + curr_batch['split_part2'].str.replace(" ","")
        if len(rl_input_df) > 0:
            len_before_filter = len(curr_batch)
            curr_batch = curr_batch[
                ~curr_batch['traj_id'].isin(rl_input_df['traj_id'])]
        curr_batch['filename'] = filename
        rl_input_df = rl_input_df.append(curr_batch, ignore_index=True)

    rl_input_df = rl_input_df.set_index('traj_id')

    # dropping exact duplicate splits
    print('size before drop dups: ' + str(len(rl_input_df)))
    rl_input_df = rl_input_df.drop_duplicates(
        ['ID', 'comp', 'split_part1', 'split_part2'])
    print('size after drop dups: ' + str(len(rl_input_df)))

    dataset_filename = '../../../mturk/compqgen/final/complexwebquestions_V1_1/ComplexWebQuestions_dev'
    with open(dataset_filename + '.json', 'r') as outfile:
        complexwebquestions = pd.DataFrame(json.load(outfile))

    rl_input_df = rl_input_df.merge(
        pd.DataFrame(complexwebquestions)[['answers', 'ID']], on='ID', how='inner')
    rl_input_df.rename(columns={'answers_y': 'answers'}, inplace=True)
    del rl_input_df['answers_x']

## Training Set

### TriviaQA

In [156]:
if USE_TRIVIAQA_TRAIN and EVAL_SET == 'train':
    with zipfile.ZipFile('../data/TriviaQA/unfiltered-web-train.json.zip','r') as myzip:
        with myzip.open('unfiltered-web-train.json') as myfile:
            questions = json.load(myfile)
            triviaqa_dataset = pd.DataFrame(questions['Data'])
            
    # empty entity pages
    triviaqa_dataset['EntityPages'] = np.empty((len(triviaqa_dataset), 0)).tolist()

    # empty search results
    triviaqa_dataset['SearchResults']  = triviaqa_dataset['SearchResults'].astype(object)
    triviaqa_dataset['SearchResults'] = np.empty((len(triviaqa_dataset), 0)).tolist()

### ComplexWebQuestions

In [157]:
if USE_COMPWEBQ_TRAIN and EVAL_SET == 'train':
    rl_input_df = pd.DataFrame()
    #data_dir = '/Users/alontalmor/Dropbox/Apps/WebKB/webkb_dev_data/RL_train_data/rl_cascade1_epoch0-8/'
    # V2 Code
    data_dir = '../data/V2_train_splitpoints/'
    for dirname, dirnames, filenames in os.walk(data_dir):

        # making sure noisy sup is added first (because of the default MIN_REWARD_TRESH values
        #if 'noisy_sup_rewarded.json.zip' in filenames:
        #    filenames.remove('noisy_sup_rewarded.json.zip')
        #    filenames = ['noisy_sup_rewarded.json.zip'] + filenames
        # V2 code
        if 'train.json.zip' in filenames:
            filenames.remove('train.json.zip')
            filenames = ['train.json.zip'] + filenames

        for filename in filenames[0:2]:

            if filename.find('.json.zip')>-1:
                print(filename)
                with zipfile.ZipFile(data_dir + filename,'r') as myzip:
                    with myzip.open(filename.replace('.zip','')) as myfile:
                        curr_batch = pd.DataFrame(json.load(myfile))
                curr_batch = curr_batch[(curr_batch[['split_part1', 'split_part2']].isnull() * 1.0).sum(axis=1) == 0] # removing null values
                # V2 Code
                if len(rl_input_df) > 0:
                    curr_batch = curr_batch[curr_batch['ID'].isin(rl_input_df['ID'])]

                curr_batch['traj_id'] = curr_batch['ID'] + curr_batch['comp'] + curr_batch['split_part1'].str.replace(" ","") \
                                            + ',' + curr_batch['split_part2'].str.replace(" ","")
                if len(rl_input_df)>0:
                    len_before_filter = len(curr_batch)
                    curr_batch = curr_batch[~curr_batch['traj_id'].isin(rl_input_df['traj_id'])]
                curr_batch['filename'] = filename
                rl_input_df = rl_input_df.append(curr_batch, ignore_index=True)

    dataset_filename = '../../../mturk/compqgen/final/complexwebquestions_V1_1/ComplexWebQuestions_train'
    with open(dataset_filename + '.json', 'r') as outfile:
        complexwebquestions = pd.DataFrame(json.load(outfile))

    rl_input_df = rl_input_df.merge(
        pd.DataFrame(complexwebquestions)[['answers', 'ID']], on='ID', how='inner')
    rl_input_df.rename(columns={'answers_y': 'answers'}, inplace=True)
    del rl_input_df['answers_x']        

    rl_input_df = rl_input_df.set_index('traj_id')

    # dropping exact duplicate splits
    print('size before drop dups: ' + str(len(rl_input_df)))
    rl_input_df = rl_input_df.drop_duplicates(['ID', 'comp', 'split_part1', 'split_part2'])
    print('size after drop dups: ' + str(len(rl_input_df)))
    
    # checking overlab between V1 training question and V2
    dataset_filename = '../../mturk/compqgen/final/complexwebquestions/ComplexWebQuestions_train'
    with open(dataset_filename + '.json', 'r') as outfile:
        complexwebquestions_org = pd.DataFrame(json.load(outfile))


In [158]:
# !! work only on sampple
if PRODUCE_ONLY_SAMPLE:
    rl_input_df = rl_input_df[0:100]

In [159]:
if USE_COMPWEBQ_TRAIN and EVAL_SET == 'train':
    dataset_filename = '../data/ComplexWebQuestions_' + EVAL_SET
    with open(dataset_filename + '.json', 'r') as outfile:
        complexwebquestions_org = pd.DataFrame(json.load(outfile)).set_index('ID')

    rl_input_df.loc[rl_input_df['comp'] == 'composition','composition_answer'] = \
        list(complexwebquestions_org.loc[rl_input_df[rl_input_df['comp'] == 'composition']['ID'],'composition_answer'].astype(object))

In [160]:
if USE_COMPWEBQ_TRAIN and EVAL_SET == 'train':
    questions = []   
    for ind in tqdm(range(len(rl_input_df)), total=len(rl_input_df), ncols=80, desc="scoring"):
        question = rl_input_df.iloc[ind]
        if question['comp'] == 'conjunction':
            q_copied = question.copy()
            questions.append(q_copied)
            if ADD_SPLITS_TO_TRAIN:
                q_copied = question.copy()
                q_copied['question'] = question['split_part1']
                questions.append(q_copied)
                q_copied = question.copy()
                q_copied['question'] = question['split_part2']
                questions.append(q_copied)
        elif question['comp'] == 'composition':
            q_copied = question.copy()
            q_copied['ID']
            questions.append(q_copied)
            if ADD_SPLITS_TO_TRAIN:
                q_copied = question.copy()
                q_copied['question'] = question['split_part1']
                q_copied['answers'] = [{'aliases':[],'answer':question['composition_answer']}]
                questions.append(q_copied)
                q_copied = question.copy()
                q_copied['question'] = question['split_part2']
                q_copied['question'] = q_copied['question'].replace('%composition',question['composition_answer'])
                questions.append(q_copied)
        else:
            q_copied = question.copy()
            questions.append(q_copied)



In [161]:
if USE_COMPWEBQ_TRAIN and EVAL_SET == 'train':
    questions = pd.DataFrame(questions)
    # dropping exact duplicate splits
    print('size before drop dups: ' + str(len(questions)))
    questions = questions.drop_duplicates(['question'])
    print('size after drop dups: ' + str(len(questions)))
    questions = questions.reset_index(drop=True)

### ComplexWebQuestions to TriviaQA format


In [162]:
if USE_COMPWEBQ_TRAIN and EVAL_SET == 'train':
    questions_triviaqa_format = pd.DataFrame()
    questions_triviaqa_format['QuestionId'] = questions['ID'] + '_' + questions.index.astype(str)
    questions_triviaqa_format['Question'] = questions['question']
    questions_triviaqa_format['SearchResults'] = [[] for x in range(len(questions_triviaqa_format))]
    questions_triviaqa_format['EntityPages'] = [[] for x in range(len(questions_triviaqa_format))]
    questions_triviaqa_format['QuestionSource'] = ''
    all_answers = []
    for ind,q in tqdm(questions.iterrows(),total=len(questions), ncols=80, desc="scoring"):
        if q['answers'][0]['answer'] == None or q['answers'][0]['answer'] == '':
            all_answers.append(None)
        else:
            filtered_answer = []
            for answer in q['answers']:
                if len(answer['answer']) > 0:
                    filtered_answer.append(answer)

            triviaqa_formated_answers = {'Aliases':[],'NormalizedAliases':[], \
                                        'NormalizedValue':'', \
                                         'Type':'FreeForm','Value':''}
            triviaqa_formated_answers['Value'] = filtered_answer[0]['answer']
            triviaqa_formated_answers['NormalizedValue'] = ' '.join(word_tokenize(filtered_answer[0]['answer'].lower()))
            for answer in filtered_answer:
                triviaqa_formated_answers['Aliases'] += answer['aliases']
                triviaqa_formated_answers['Aliases'].append(answer['answer'])

            triviaqa_formated_answers['NormalizedAliases'] = \
                [' '.join(word_tokenize(word.lower())) for word in triviaqa_formated_answers['Aliases']]
            all_answers.append(triviaqa_formated_answers)

    questions_triviaqa_format['Answer'] = all_answers
    questions_triviaqa_format = questions_triviaqa_format[questions_triviaqa_format['Answer'].notnull()]  

### combine all training sets


In [163]:
# combining all the training sets
if USE_TRIVIAQA_TRAIN and USE_COMPWEBQ_TRAIN and EVAL_SET == 'train':
    print('Combining triviaqa and complexwebquestions')
    print(len(questions_triviaqa_format))
    print(len(triviaqa_dataset))
    questions_triviaqa_format = questions_triviaqa_format.append(triviaqa_dataset,ignore_index=True)
    print(len(questions_triviaqa_format))
elif USE_TRIVIAQA_TRAIN and EVAL_SET == 'train':
    print('Using only triviaqa for training')
    questions_triviaqa_format = triviaqa_dataset

Using only triviaqa for training


### choose dev set


In [164]:
if USE_TRIVIAQA_DEV and EVAL_SET == 'dev':
    questions_triviaqa_format = triviaqa_dataset

# Appending snippets to the questions

## From local mongo

In [165]:
if not SEARCHRESULTS_FROM_FILES:
    MONGODB_URI = 'mongodb://127.0.0.1:27017/webkb'
    mongo_client = pymongo.MongoClient(MONGODB_URI)
    db = mongo_client.get_default_database()
    SearchCache = db['SearchResults_Cache']

In [166]:
if not SEARCHRESULTS_FROM_FILES:
    found = 0
    questions_triviaqa_format['SearchResults'] = None
    questions_triviaqa_format['SearchResults'] = questions_triviaqa_format['SearchResults'].astype(object)
    for ind in tqdm(range(len(questions_triviaqa_format)), total=len(questions_triviaqa_format), ncols=80,\
                    desc="appending google search results"):
        question  = questions_triviaqa_format.iloc[ind]
        CacheResults = SearchCache.find(
            {'querystr': question['Question'], "page": 0, "type": 'SCREEN'})
        CacheResults_Count = CacheResults.count()
        if CacheResults_Count>0:
            found += 1
            cahched_item = CacheResults.next()
            questions_triviaqa_format.at[ind,'SearchResults'] = cahched_item['results']

## From files

In [167]:
if SEARCHRESULTS_FROM_FILES:
    if EVAL_SET == 'dev':
        googled_dir = '../data/triviaqa_googled_dev'
    else:
        googled_dir = '../data/triviaqa_googled_train'

    questions_triviaqa_format = questions_triviaqa_format.set_index('QuestionId')
    questions_triviaqa_format['SearchResults'] = None
    questions_triviaqa_format['SearchResults'] = questions_triviaqa_format['SearchResults'].astype(object)

    for dirname, dirnames, filenames in os.walk(googled_dir):
        for filename in tqdm(filenames, total=len(filenames), ncols=80, desc='iterating over all googled files'):
            with zipfile.ZipFile(googled_dir + '/' + filename,'r') as myzip:
                with myzip.open(filename.replace('.zip','')) as myfile:
                    googled = json.load(myfile)

            for googled_question in googled:
                questions_triviaqa_format.at[googled_question['QuestionId'],\
                                             'SearchResults'] = googled_question['google_results']

    questions_triviaqa_format = questions_triviaqa_format.reset_index()
    
    found = (questions_triviaqa_format['SearchResults'].notnull()).sum()


iterating over all googled files: 100%|███████| 383/383 [00:38<00:00,  9.98it/s]


In [168]:
print(found)

questions_triviaqa_format = questions_triviaqa_format[questions_triviaqa_format['SearchResults'].notnull()]

print(len(questions_triviaqa_format))

questions_triviaqa_format = questions_triviaqa_format[questions_triviaqa_format['Answer'].notnull()]  

76496
76496


In [169]:
print('sanity check for nulls in data')
questions_triviaqa_format.isnull().sum()

sanity check for nulls in data


QuestionId        0
Answer            0
EntityPages       0
Question          0
QuestionSource    0
SearchResults     0
dtype: int64

# Building Evidence Files

In [170]:
print('checking if there exist cases in which there are no answers?')
print(len(questions_triviaqa_format[questions_triviaqa_format['Answer'].agg(lambda x: x['Value']).apply(len)==0]['Answer']))

checking if there exist cases in which there are no answers?
0


In [171]:
triviaqa_dict = {}
triviaqa_dict['Data'] = questions_triviaqa_format
triviaqa_dict['Domain'] = 'unfiltered-web'
triviaqa_dict['Split'] = EVAL_SET
triviaqa_dict['VerifiedEval'] = False
triviaqa_dict['Version'] = 1.0

In [172]:
data_df = triviaqa_dict['Data']
data_df = data_df.set_index('QuestionId')
org_data_df = data_df.copy(deep=True)
data_df = data_df.rename(columns = {'SearchResults':'OrgSearchResults'})
data_df['SearchResults'] = None

In [173]:
# create a query to file map

if WRITE_EVIDENCE and not os.path.isdir(EVIDENCE_DIR + 'evidence/'):
    os.mkdir(EVIDENCE_DIR + 'evidence/')

if WRITE_EVIDENCE and not os.path.isdir(EVIDENCE_DIR +'evidence/' + EXP_NAME):
    os.mkdir(EVIDENCE_DIR + 'evidence/' + EXP_NAME)
        
train_file_ind = int(0)
for i in tqdm(range(len(data_df)), total=len(data_df), ncols=80, desc="building evidence files"):
    question = data_df.iloc[i]
    questionID = data_df.index[i]
    # building 10 text files out of 100 snippets
    SearchResults = []
    files = []
    filenames = []
    file_ind = 0
    google_results = question['OrgSearchResults']
    train_file_ind += 1
    
        
    if WRITE_EVIDENCE and not os.path.isdir(EVIDENCE_DIR + 'evidence/' + EXP_NAME + '/' + str(int(train_file_ind / 100))):
        os.mkdir(EVIDENCE_DIR + 'evidence/' + EXP_NAME + '/' + str(int(train_file_ind / 100)))
        #if train_file_ind % 1000 == 0:
        #    print(EVIDENCE_DIR + 'evidence/' + EXP_NAME + '/' + str(int(train_file_ind / 100)))

    for ind, g in enumerate(google_results):
        file_ind = file_ind % FILES_PER_QUESTION
        if len(files) <= file_ind:
            file_name = EXP_NAME + '/' + str(int(train_file_ind / 100)) + "/" + \
                questionID + '_' + str(file_ind) + '.txt'
            SearchResults.append({'Rank':ind, 'Description':g['snippet'],'Title':g['title'],'DisplayUrl':g['url'] , \
                          'Url':g['url'] + file_name.replace('/','_').replace('.txt',''),'Filename':file_name })
            files.append('')
            filenames.append(file_name)

        files[file_ind] += str(
            ind) + '. ' + g['title'] + '\n' + g['snippet'] + '\n'

        file_ind += 1

    # saving files
    if WRITE_EVIDENCE:
        for file_str, file_name in zip(files, filenames):
            with open(EVIDENCE_DIR + 'evidence/' + file_name, 'w') as outfile:
                outfile.write(file_str)

    data_df.at[questionID, 'SearchResults'] = SearchResults

building evidence files: 100%|███████████| 76496/76496 [08:34<00:00, 148.65it/s]


# Calc answer in google percentage

In [174]:
if CALC_ANSWER_IN_GOOGLE_PERC:
    answer_found_mat = np.zeros((len(data_df),100))
    q_ind = 0
    for ind,question in tqdm(data_df.iterrows(),total=len(data_df), ncols=80, \
                             desc='checking how many gold answer are within question snippets'):
        normalized_aliases = question['Answer']['NormalizedAliases']

        for s_ind,result in enumerate(question['SearchResults']):
            for alias in normalized_aliases:
                result_text = result['Title'] + ' ' + result['Description']
                p = re.compile(r'\b({0})\b'.format(alias), re.IGNORECASE)
                res = re.findall(p, result_text)
                #if result_text.find(alias)>-1:
                 #   answer_found_mat[q_ind , s_ind] = 1
                if len(res) > 0:
                    answer_found_mat[q_ind , s_ind] = 1
                    break
        q_ind += 1
                #else:
                #    print(alias + ' --- ' + result_text)
    
    print('answer are within question snippets {0}%'.format(100.0* (answer_found_mat.sum(axis=1)>0).sum() / len(data_df)))

checking how many gold answer are within question snippets: 100%|█| 76496/76496 [07:50<00:00, 162.57it/s]


answer are within question snippets 88.87915708010877%


# Sanity Tests

In [175]:
# additional sanity tests
(data_df.isnull()).sum()

Answer              0
EntityPages         0
Question            0
QuestionSource      0
OrgSearchResults    0
SearchResults       0
dtype: int64

In [176]:
# additional sanity tests
data_df['SearchResults'].apply(len).value_counts()

20    71655
0      2548
2       826
3       365
4       198
5       155
6       104
7        82
10       68
9        60
11       52
13       50
18       48
17       47
14       47
8        46
15       42
19       39
12       33
16       31
Name: SearchResults, dtype: int64

In [177]:
found = 0
not_found = 0
for i in tqdm(range(len(data_df)), total=len(data_df), ncols=80, desc="checking if filenames exist"):
    question = data_df.iloc[i]
    questionID = data_df.index[i]
    for ind, g in enumerate(question['SearchResults']):
        if os.path.exists(EVIDENCE_DIR + 'evidence/' + g['Filename']):
            found += 1
        else:
            not_found += 1

print('found : {0}'.format(found))
print('not_found : {0}'.format(not_found))

checking if filenames exist: 100%|███████| 76496/76496 [02:27<00:00, 520.03it/s]

found : 1446006
not_found : 0


# saving 

In [178]:
del data_df['OrgSearchResults']

# randomizing the samples:
data_df = data_df.sample(frac=1)

if not os.path.isdir('../output/' ):
    os.mkdir('../output/' )
if not os.path.isdir('../output/' + EXP_NAME):
    os.mkdir('../output/' + EXP_NAME)

if EVAL_SET == 'dev':
    triviaqa_dict['Data'] = data_df.reset_index().to_dict(orient='rows')
    with zipfile.ZipFile('../output/' + EXP_NAME + '/' + "unfiltered-web-dev.json.zip", "w", zipfile.ZIP_DEFLATED) as zip_file:
        zip_file.writestr('unfiltered-web-dev.json', json.dumps(triviaqa_dict, sort_keys=True, indent=4))
else:
    triviaqa_dict['Data'] = data_df.reset_index().to_dict(orient='rows')
    with zipfile.ZipFile('../output/' + EXP_NAME + '/' + "unfiltered-web-train.json.zip", "w", zipfile.ZIP_DEFLATED) as zip_file:
        zip_file.writestr('unfiltered-web-train.json', json.dumps(triviaqa_dict, sort_keys=True, indent=4))

# experiments

In [182]:
if True:
     with zipfile.ZipFile('/Users/alontalmor/Documents/dev/datasets/squad2_0/dev-v2.0.json.zip','r') as myzip:
        with myzip.open('dev-v2.0.json') as myfile:
            squad_dev = json.load(myfile)
            squad_dev_df = pd.DataFrame(squad_dev['data'])
     

In [183]:
squad_dev

{'data': [{'paragraphs': [{'context': 'The Normans (Norman: Nourmands; French: Normands; Latin: Normanni) were the people who in the 10th and 11th centuries gave their name to Normandy, a region in France. They were descended from Norse ("Norman" comes from "Norseman") raiders and pirates from Denmark, Iceland and Norway who, under their leader Rollo, agreed to swear fealty to King Charles III of West Francia. Through generations of assimilation and mixing with the native Frankish and Roman-Gaulish populations, their descendants would gradually merge with the Carolingian-based cultures of West Francia. The distinct cultural and ethnic identity of the Normans emerged initially in the first half of the 10th century, and it continued to evolve over the succeeding centuries.',
     'qas': [{'answers': [{'answer_start': 159, 'text': 'France'},
        {'answer_start': 159, 'text': 'France'},
        {'answer_start': 159, 'text': 'France'},
        {'answer_start': 159, 'text': 'France'}],
 